In [18]:
import os
import random
import shutil

from pathlib import Path
import numpy as np

# import dlib
# import MTCNN

import torch
from PIL import Image
from torch.utils.data import Dataset
from torchvision import transforms
from torch.utils.data import DataLoader
from facenet_pytorch import MTCNN


# from utils import load_image_and_preprocess

import cv2
import torch
import numpy as np
from pathlib import Path

from tqdm.notebook import tqdm, trange

### function from utils.py to construct our input images

In [53]:
def load_image_and_preprocess(image_filename, output_image_size, face_detector):
    # read in image with cv2

    image_raw = cv2.imread(image_filename)

    #this might not be needed to correct for color space
#     image = cv2.cvtColor(image_raw, cv2.COLOR_BGR2RGB)
    image = cv2.imread(image_filename)
    
    h, w = image.shape[:2]
    #print("H: ", h)
    #print("W: ", w)
    
    if h < 50 or w < 50:
        #print("image too small")
        return None
    

    # #use first face detected and check if there were none
    boxes, confidence = face_detector.detect(image_raw)

    if boxes is None:
        return None


    # bounding_box = result[0]["box"]
    bounding_box = boxes[0]
    #collect image height and width
    height, width = image.shape[:2]

    #set scaling factor
    scale=0.98

    #collect coordinates of bounding box
    x1 = bounding_box[0] #dib face.left
    y1 = bounding_box[1] #dib face.top
    x2 = bounding_box[2] #dib face.right
    y2 = bounding_box[3] #dib face.bottom

    #scale bounding box?
    size_bb = int(max(x2 - x1, y2 - y1) * scale)

    #control for out of bounds, x-y top left corner
    center_x, center_y = (x1 + x2) // 2, (y1 + y2) // 2
    x1 = max(int(center_x - size_bb // 2), 0)
    y1 = max(int(center_y - size_bb // 2), 0)

    # Check for too big bb size for given x, y
    size_bb = min(width - x1, size_bb)
    size_bb = min(height - y1, size_bb)

    # set up for crop with slicing
    cropped_face = image[y1:y1 + size_bb, x1:x1 + size_bb]

    resized_image = cv2.resize(cropped_face, (output_image_size, output_image_size))
    return resized_image

In [20]:
def dont():
    return 1

In [28]:
def process_directories(source_paths_list, destination_path, face_detector):
    for path in tqdm(source_paths_list):
        src_file_list = os.listdir(path)

        print(f"moving {len(src_file_list)} files found in path:\n  {path}")
        none_count=0
        
       
        
        for file in tqdm(src_file_list):
            #TODO save misses to .txt file?
            
            filename = os.path.join(path, file)
            img_result = load_image_and_preprocess(filename, 224, face_detector)
            
            if img_result is None:
                none_count+=1
                #print("-", file)
                #.txt file write file
                
            else:
                #dont()
                cv2.imwrite(os.path.join(destination_path, file), img_result)
                #print("saving file: ", file)
        
            
        
        print(f"of {len(src_file_list)}, there were {none_count} missed detections\n\n")

collect the gpu if possible for MTCNN

In [29]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print("device: ", device)

device:  cuda:0


intialize MTCNN

In [32]:
face_detector = MTCNN(select_largest=True, thresholds=[0.4, 0.6, 0.8], device=device)

#### I am now going to take all of the raw images from the mask and no mask directories and pass them through mtcnn and store the output faces in a seperate directory to be used during training


In [54]:
#path to source directories for MASKED FACES

mask_src_paths = ["E:/One Drive/OneDrive/Mainproject/MaskLockData/data_11_28_2020_pngs", 
             "E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset/medical_mask_archive-processed", 
             "E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset/face_mask_detection_archive-processed"]

mask_dest_path = "E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset_mtcnn-results"



In [55]:
process_directories(mask_src_paths, mask_dest_path, face_detector)

moving 425 files found in path:
  E:/One Drive/OneDrive/Mainproject/MaskLockData/data_11_28_2020_pngs



of 425, there were 204 missed detections


moving 4067 files found in path:
  E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset/medical_mask_archive-processed



of 4067, there were 2988 missed detections


moving 3232 files found in path:
  E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset/face_mask_detection_archive-processed



of 3232, there were 2613 missed detections





In [71]:
for i in:

SyntaxError: invalid syntax (<ipython-input-71-4c05b4aec206>, line 1)

In [36]:
#path to source directories for UNMASKED FACES

un_src_paths = ["E:/One Drive/OneDrive/Mainproject/MaskLockData/no_mask_dataset"]

un_dest_path = "E:/One Drive/OneDrive/Mainproject/MaskLockData/no_mask_dataset_mtcnn-results"

In [37]:
# process_directories(un_src_paths, un_dest_path) face_detector

moving 52001 files found in path:
  E:/One Drive/OneDrive/Mainproject/MaskLockData/no_mask_dataset



of 52001, there were 845 missed detections





## I am now going to partition the dataset into train/test sets 

In [57]:
def train_test_split(train_path, val_path, source_path):
    print(f"performing 80/20 train/val split on: \n{source_path}")
    
    source_file_list = os.listdir(source_path)
    
    random.shuffle(source_file_list) #make sure they're in random order
    
    eighty_lst = source_file_list[:int(len(source_file_list)*0.8)] #grab 80% percent for training
    
    twenty_list = [] #collect only the ones not already in train-set for val

    for file in source_file_list:
        if file not in eighty_lst:
            twenty_list.append(file)
    
    print(f"total files: {len(source_file_list)}")
    print(f"train will contain: {len(eighty_lst)} files")
    print(f"val will contain: {len(twenty_list)} files")
    
    #move the files to be used in training
    for file in tqdm(eighty_lst):
        shutil.copy(os.path.join(source_path, file), os.path.join(train_path, file))
        
    
    #move the files to be used for validation
    for file in tqdm(twenty_list):
        shutil.copy(os.path.join(source_path, file), os.path.join(val_path, file))
        
    
    

In [83]:
train_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/mask"
val_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/mask"

mask_path = "E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset_mtcnn-results"

In [84]:
#Masked Dataset
train_test_split(train_mask_dest, val_mask_dest, mask_path)

performing 80/20 train/val split on: 
E:/One Drive/OneDrive/Mainproject/MaskLockData/mask_dataset_mtcnn-results
total files: 1766
train will contain: 1412 files
val will contain: 354 files


In [60]:
train_no_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/no_mask"
val_no_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/no_mask"

no_mask_path = "E:/One Drive/OneDrive/Mainproject/MaskLockData/no_mask_dataset_mtcnn-results"

In [61]:
train_test_split(train_no_mask_dest, val_no_mask_dest, no_mask_path)

performing 80/20 train/val split on: 
E:/One Drive/OneDrive/Mainproject/MaskLockData/no_mask_dataset_mtcnn-results
total files: 51081
train will contain: 40864 files
val will contain: 10217 files


# ...and over-sample by duplication the MASKED set

In [85]:
import random
import string

def get_random_string(length):
    letters = string.ascii_lowercase
    result_str = ''.join(random.choice(letters) for i in range(length))
    return result_str

In [89]:
def up_sample(dataset_to_match_path, source_to_upsample_path, upsample_dest_path):
    
    print("files in smaller class: ",len(os.listdir(upsample_dest_path)))
    print("files in larger class: ",len(os.listdir(dataset_to_match_path)))
    
    #copy files from source to dest
    print("copying files to directory where they will be upsampled:")
    print("source:  ", source_to_upsample_path)
    print("destination: ", upsample_dest_path)
    
    #get static list of files in new dir first
    files_to_choose_from = os.listdir(source_to_upsample_path)
    
    #now for dest use random choice to upsample to match the other dataset   
    count = 0
    while len(os.listdir(upsample_dest_path)) != len(os.listdir(dataset_to_match_path)):
        file = random.choice(files_to_choose_from)
        
        #collect a random string to prevent overwritting
        new_filename = file.split('.')[0]+get_random_string(10)+'.png'
        
        #print(new_filename)
        #print(len(os.listdir(upsample_dest_path)))
        #print(len(os.listdir(dataset_to_match_path)))
        
        #copy from source to dest
        shutil.copy(os.path.join(source_to_upsample_path, file), os.path.join(upsample_dest_path, new_filename))
        if count%100 == 0:
            print("current no. in smaller class: ",len(os.listdir(upsample_dest_path)))
            print("current no. in larger class: ",len(os.listdir(dataset_to_match_path)))
            
        count+=1
    print(f"done.. now there are {len(os.listdir(upsample_dest_path))} files in the destination")

In [90]:
#validation set up_sampling

# source:
val_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/mask"
#dest:
up_val_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask"
#matching:
val_no_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/no_mask"

up_sample(val_no_mask_dest, val_mask_dest, up_val_mask_dest)

files in smaller class:  0
files in larger class:  10217
copying files to directory where they will be upsampled:
source:   E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/mask
destination:  E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask
current no. in smaller class:  1
current no. in larger class:  10217
current no. in smaller class:  2
current no. in larger class:  10217
current no. in smaller class:  3
current no. in larger class:  10217
current no. in smaller class:  4
current no. in larger class:  10217
current no. in smaller class:  5
current no. in larger class:  10217
current no. in smaller class:  6
current no. in larger class:  10217
current no. in smaller class:  7
current no. in larger class:  10217
current no. in smaller class:  8
current no. in larger class:  10217
current no. in smaller class:  9
current no. in larger class:  10217
current no. in smaller class:  10
current no. in larger class:  10217
current no. in smaller class:  11
curr

current no. in larger class:  10217
current no. in smaller class:  121
current no. in larger class:  10217
current no. in smaller class:  122
current no. in larger class:  10217
current no. in smaller class:  123
current no. in larger class:  10217
current no. in smaller class:  124
current no. in larger class:  10217
current no. in smaller class:  125
current no. in larger class:  10217
current no. in smaller class:  126
current no. in larger class:  10217
current no. in smaller class:  127
current no. in larger class:  10217
current no. in smaller class:  128
current no. in larger class:  10217
current no. in smaller class:  129
current no. in larger class:  10217
current no. in smaller class:  130
current no. in larger class:  10217
current no. in smaller class:  131
current no. in larger class:  10217
current no. in smaller class:  132
current no. in larger class:  10217
current no. in smaller class:  133
current no. in larger class:  10217
current no. in smaller class:  134
curren

current no. in smaller class:  236
current no. in larger class:  10217
current no. in smaller class:  237
current no. in larger class:  10217
current no. in smaller class:  238
current no. in larger class:  10217
current no. in smaller class:  239
current no. in larger class:  10217
current no. in smaller class:  240
current no. in larger class:  10217
current no. in smaller class:  241
current no. in larger class:  10217
current no. in smaller class:  242
current no. in larger class:  10217
current no. in smaller class:  243
current no. in larger class:  10217
current no. in smaller class:  244
current no. in larger class:  10217
current no. in smaller class:  245
current no. in larger class:  10217
current no. in smaller class:  246
current no. in larger class:  10217
current no. in smaller class:  247
current no. in larger class:  10217
current no. in smaller class:  248
current no. in larger class:  10217
current no. in smaller class:  249
current no. in larger class:  10217
curren

current no. in larger class:  10217
current no. in smaller class:  356
current no. in larger class:  10217
current no. in smaller class:  357
current no. in larger class:  10217
current no. in smaller class:  358
current no. in larger class:  10217
current no. in smaller class:  359
current no. in larger class:  10217
current no. in smaller class:  360
current no. in larger class:  10217
current no. in smaller class:  361
current no. in larger class:  10217
current no. in smaller class:  362
current no. in larger class:  10217
current no. in smaller class:  363
current no. in larger class:  10217
current no. in smaller class:  364
current no. in larger class:  10217
current no. in smaller class:  365
current no. in larger class:  10217
current no. in smaller class:  366
current no. in larger class:  10217
current no. in smaller class:  367
current no. in larger class:  10217
current no. in smaller class:  368
current no. in larger class:  10217
current no. in smaller class:  369
curren

current no. in larger class:  10217
current no. in smaller class:  480
current no. in larger class:  10217
current no. in smaller class:  481
current no. in larger class:  10217
current no. in smaller class:  482
current no. in larger class:  10217
current no. in smaller class:  483
current no. in larger class:  10217
current no. in smaller class:  484
current no. in larger class:  10217
current no. in smaller class:  485
current no. in larger class:  10217
current no. in smaller class:  486
current no. in larger class:  10217
current no. in smaller class:  487
current no. in larger class:  10217
current no. in smaller class:  488
current no. in larger class:  10217
current no. in smaller class:  489
current no. in larger class:  10217
current no. in smaller class:  490
current no. in larger class:  10217
current no. in smaller class:  491
current no. in larger class:  10217
current no. in smaller class:  492
current no. in larger class:  10217
current no. in smaller class:  493
curren

...

current no. in smaller class:  9753
current no. in larger class:  10217
current no. in smaller class:  9754
current no. in larger class:  10217
current no. in smaller class:  9755
current no. in larger class:  10217
current no. in smaller class:  9756
current no. in larger class:  10217
current no. in smaller class:  9757
current no. in larger class:  10217
current no. in smaller class:  9758
current no. in larger class:  10217
current no. in smaller class:  9759
current no. in larger class:  10217
current no. in smaller class:  9760
current no. in larger class:  10217
current no. in smaller class:  9761
current no. in larger class:  10217
current no. in smaller class:  9762
current no. in larger class:  10217
current no. in smaller class:  9763
current no. in larger class:  10217
current no. in smaller class:  9764
current no. in larger class:  10217
current no. in smaller class:  9765
current no. in larger class:  10217
current no. in smaller class:  9766
current no. in larger class:

current no. in smaller class:  9869
current no. in larger class:  10217
current no. in smaller class:  9870
current no. in larger class:  10217
current no. in smaller class:  9871
current no. in larger class:  10217
current no. in smaller class:  9872
current no. in larger class:  10217
current no. in smaller class:  9873
current no. in larger class:  10217
current no. in smaller class:  9874
current no. in larger class:  10217
current no. in smaller class:  9875
current no. in larger class:  10217
current no. in smaller class:  9876
current no. in larger class:  10217
current no. in smaller class:  9877
current no. in larger class:  10217
current no. in smaller class:  9878
current no. in larger class:  10217
current no. in smaller class:  9879
current no. in larger class:  10217
current no. in smaller class:  9880
current no. in larger class:  10217
current no. in smaller class:  9881
current no. in larger class:  10217
current no. in smaller class:  9882
current no. in larger class:

current no. in smaller class:  9984
current no. in larger class:  10217
current no. in smaller class:  9985
current no. in larger class:  10217
current no. in smaller class:  9986
current no. in larger class:  10217
current no. in smaller class:  9987
current no. in larger class:  10217
current no. in smaller class:  9988
current no. in larger class:  10217
current no. in smaller class:  9989
current no. in larger class:  10217
current no. in smaller class:  9990
current no. in larger class:  10217
current no. in smaller class:  9991
current no. in larger class:  10217
current no. in smaller class:  9992
current no. in larger class:  10217
current no. in smaller class:  9993
current no. in larger class:  10217
current no. in smaller class:  9994
current no. in larger class:  10217
current no. in smaller class:  9995
current no. in larger class:  10217
current no. in smaller class:  9996
current no. in larger class:  10217
current no. in smaller class:  9997
current no. in larger class:

current no. in smaller class:  10099
current no. in larger class:  10217
current no. in smaller class:  10100
current no. in larger class:  10217
current no. in smaller class:  10101
current no. in larger class:  10217
current no. in smaller class:  10102
current no. in larger class:  10217
current no. in smaller class:  10103
current no. in larger class:  10217
current no. in smaller class:  10104
current no. in larger class:  10217
current no. in smaller class:  10105
current no. in larger class:  10217
current no. in smaller class:  10106
current no. in larger class:  10217
current no. in smaller class:  10107
current no. in larger class:  10217
current no. in smaller class:  10108
current no. in larger class:  10217
current no. in smaller class:  10109
current no. in larger class:  10217
current no. in smaller class:  10110
current no. in larger class:  10217
current no. in smaller class:  10111
current no. in larger class:  10217
current no. in smaller class:  10112
current no. in

current no. in smaller class:  10212
current no. in larger class:  10217
current no. in smaller class:  10213
current no. in larger class:  10217
current no. in smaller class:  10214
current no. in larger class:  10217
current no. in smaller class:  10215
current no. in larger class:  10217
current no. in smaller class:  10216
current no. in larger class:  10217
current no. in smaller class:  10217
current no. in larger class:  10217
done.. now there are 10217 files in the destination


In [91]:
#training set up_sampling

#source:
train_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/mask"
#dest:
up_train_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/up_mask"
#matching:
train_no_mask_dest = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/no_mask"

up_sample(train_no_mask_dest, train_mask_dest, up_train_mask_dest)

files in smaller class:  0
files in larger class:  40864
copying files to directory where they will be upsampled:
source:   E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/mask
destination:  E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/train/up_mask
current no. in smaller class:  1
current no. in larger class:  40864
current no. in smaller class:  2
current no. in larger class:  40864
current no. in smaller class:  3
current no. in larger class:  40864
current no. in smaller class:  4
current no. in larger class:  40864
current no. in smaller class:  5
current no. in larger class:  40864
current no. in smaller class:  6
current no. in larger class:  40864
current no. in smaller class:  7
current no. in larger class:  40864
current no. in smaller class:  8
current no. in larger class:  40864
current no. in smaller class:  9
current no. in larger class:  40864
current no. in smaller class:  10
current no. in larger class:  40864
current no. in smaller class:  11


current no. in larger class:  40864
current no. in smaller class:  117
current no. in larger class:  40864
current no. in smaller class:  118
current no. in larger class:  40864
current no. in smaller class:  119
current no. in larger class:  40864
current no. in smaller class:  120
current no. in larger class:  40864
current no. in smaller class:  121
current no. in larger class:  40864
current no. in smaller class:  122
current no. in larger class:  40864
current no. in smaller class:  123
current no. in larger class:  40864
current no. in smaller class:  124
current no. in larger class:  40864
current no. in smaller class:  125
current no. in larger class:  40864
current no. in smaller class:  126
current no. in larger class:  40864
current no. in smaller class:  127
current no. in larger class:  40864
current no. in smaller class:  128
current no. in larger class:  40864
current no. in smaller class:  129
current no. in larger class:  40864
current no. in smaller class:  130
curren

current no. in larger class:  40864
current no. in smaller class:  234
current no. in larger class:  40864
current no. in smaller class:  235
current no. in larger class:  40864
current no. in smaller class:  236
current no. in larger class:  40864
current no. in smaller class:  237
current no. in larger class:  40864
current no. in smaller class:  238
current no. in larger class:  40864
current no. in smaller class:  239
current no. in larger class:  40864
current no. in smaller class:  240
current no. in larger class:  40864
current no. in smaller class:  241
current no. in larger class:  40864
current no. in smaller class:  242
current no. in larger class:  40864
current no. in smaller class:  243
current no. in larger class:  40864
current no. in smaller class:  244
current no. in larger class:  40864
current no. in smaller class:  245
current no. in larger class:  40864
current no. in smaller class:  246
current no. in larger class:  40864
current no. in smaller class:  247
curren

current no. in larger class:  40864
current no. in smaller class:  351
current no. in larger class:  40864
current no. in smaller class:  352
current no. in larger class:  40864
current no. in smaller class:  353
current no. in larger class:  40864
current no. in smaller class:  354
current no. in larger class:  40864
current no. in smaller class:  355
current no. in larger class:  40864
current no. in smaller class:  356
current no. in larger class:  40864
current no. in smaller class:  357
current no. in larger class:  40864
current no. in smaller class:  358
current no. in larger class:  40864
current no. in smaller class:  359
current no. in larger class:  40864
current no. in smaller class:  360
current no. in larger class:  40864
current no. in smaller class:  361
current no. in larger class:  40864
current no. in smaller class:  362
current no. in larger class:  40864
current no. in smaller class:  363
current no. in larger class:  40864
current no. in smaller class:  364
curren

current no. in smaller class:  467
current no. in larger class:  40864
current no. in smaller class:  468
current no. in larger class:  40864
current no. in smaller class:  469
current no. in larger class:  40864
current no. in smaller class:  470
current no. in larger class:  40864
current no. in smaller class:  471
current no. in larger class:  40864
current no. in smaller class:  472
current no. in larger class:  40864
current no. in smaller class:  473
current no. in larger class:  40864
current no. in smaller class:  474
current no. in larger class:  40864
current no. in smaller class:  475
current no. in larger class:  40864
current no. in smaller class:  476
current no. in larger class:  40864
current no. in smaller class:  477
current no. in larger class:  40864
current no. in smaller class:  478
current no. in larger class:  40864
current no. in smaller class:  479
current no. in larger class:  40864
current no. in smaller class:  480
current no. in larger class:  40864
curren

...

current no. in smaller class:  40400
current no. in larger class:  40864
current no. in smaller class:  40401
current no. in larger class:  40864
current no. in smaller class:  40402
current no. in larger class:  40864
current no. in smaller class:  40403
current no. in larger class:  40864
current no. in smaller class:  40404
current no. in larger class:  40864
current no. in smaller class:  40405
current no. in larger class:  40864
current no. in smaller class:  40406
current no. in larger class:  40864
current no. in smaller class:  40407
current no. in larger class:  40864
current no. in smaller class:  40408
current no. in larger class:  40864
current no. in smaller class:  40409
current no. in larger class:  40864
current no. in smaller class:  40410
current no. in larger class:  40864
current no. in smaller class:  40411
current no. in larger class:  40864
current no. in smaller class:  40412
current no. in larger class:  40864
current no. in smaller class:  40413
current no. in

current no. in smaller class:  40513
current no. in larger class:  40864
current no. in smaller class:  40514
current no. in larger class:  40864
current no. in smaller class:  40515
current no. in larger class:  40864
current no. in smaller class:  40516
current no. in larger class:  40864
current no. in smaller class:  40517
current no. in larger class:  40864
current no. in smaller class:  40518
current no. in larger class:  40864
current no. in smaller class:  40519
current no. in larger class:  40864
current no. in smaller class:  40520
current no. in larger class:  40864
current no. in smaller class:  40521
current no. in larger class:  40864
current no. in smaller class:  40522
current no. in larger class:  40864
current no. in smaller class:  40523
current no. in larger class:  40864
current no. in smaller class:  40524
current no. in larger class:  40864
current no. in smaller class:  40525
current no. in larger class:  40864
current no. in smaller class:  40526
current no. in

current no. in smaller class:  40626
current no. in larger class:  40864
current no. in smaller class:  40627
current no. in larger class:  40864
current no. in smaller class:  40628
current no. in larger class:  40864
current no. in smaller class:  40629
current no. in larger class:  40864
current no. in smaller class:  40630
current no. in larger class:  40864
current no. in smaller class:  40631
current no. in larger class:  40864
current no. in smaller class:  40632
current no. in larger class:  40864
current no. in smaller class:  40633
current no. in larger class:  40864
current no. in smaller class:  40634
current no. in larger class:  40864
current no. in smaller class:  40635
current no. in larger class:  40864
current no. in smaller class:  40636
current no. in larger class:  40864
current no. in smaller class:  40637
current no. in larger class:  40864
current no. in smaller class:  40638
current no. in larger class:  40864
current no. in smaller class:  40639
current no. in

current no. in smaller class:  40739
current no. in larger class:  40864
current no. in smaller class:  40740
current no. in larger class:  40864
current no. in smaller class:  40741
current no. in larger class:  40864
current no. in smaller class:  40742
current no. in larger class:  40864
current no. in smaller class:  40743
current no. in larger class:  40864
current no. in smaller class:  40744
current no. in larger class:  40864
current no. in smaller class:  40745
current no. in larger class:  40864
current no. in smaller class:  40746
current no. in larger class:  40864
current no. in smaller class:  40747
current no. in larger class:  40864
current no. in smaller class:  40748
current no. in larger class:  40864
current no. in smaller class:  40749
current no. in larger class:  40864
current no. in smaller class:  40750
current no. in larger class:  40864
current no. in smaller class:  40751
current no. in larger class:  40864
current no. in smaller class:  40752
current no. in

current no. in smaller class:  40852
current no. in larger class:  40864
current no. in smaller class:  40853
current no. in larger class:  40864
current no. in smaller class:  40854
current no. in larger class:  40864
current no. in smaller class:  40855
current no. in larger class:  40864
current no. in smaller class:  40856
current no. in larger class:  40864
current no. in smaller class:  40857
current no. in larger class:  40864
current no. in smaller class:  40858
current no. in larger class:  40864
current no. in smaller class:  40859
current no. in larger class:  40864
current no. in smaller class:  40860
current no. in larger class:  40864
current no. in smaller class:  40861
current no. in larger class:  40864
current no. in smaller class:  40862
current no. in larger class:  40864
current no. in smaller class:  40863
current no. in larger class:  40864
current no. in smaller class:  40864
current no. in larger class:  40864
done.. now there are 40864 files in the destination

# Now I'm going to investigate the functionality of the dataloader 
#### specifically, I'm going to create our dataloaders the same way as in the model and then plot some batches and labels

In [176]:
from pathlib import Path
import numpy as np

import torch
from PIL import Image
from torch.utils.data import Dataset
from torchvision import transforms
from torch.utils.data import DataLoader, BatchSampler, RandomSampler

import cv2

# import matplotlib.pyplot as plt

In [241]:
# def collate_fn(batch):
#     imgs = [item['image'] for item in batch if item['image'] is not None]
#     targets = [item['label'] for item in batch if item['image'] is not None]
#     filenames = [item['filename'] for item in batch if item['image'] is not None]
#     imgs = torch.stack(imgs)
#     targets = torch.stack(targets)
#     return {'image': imgs, 'label': targets, 'filename': filenames}

def compose_transforms():
    pre_trained_mean, pre_trained_std = [0.485, 0.456, 0.406], [0.229, 0.224, 0.225]
    
    train_transforms = transforms.Compose([
        transforms.RandomHorizontalFlip(),
        # transforms.RandomAffine(degrees=40, scale=(.9, 1.1), shear=0),
        transforms.RandomPerspective(distortion_scale=0.2),
        # transforms.ColorJitter(brightness=0.5, contrast=0.5, saturation=0.5),
        transforms.ToTensor(),
        # transforms.RandomErasing(scale=(0.02, 0.16), ratio=(0.3, 1.6)),
        transforms.Normalize(mean=pre_trained_mean, std=pre_trained_std),
    ])
    
    val_transforms = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize(mean=pre_trained_mean, std=pre_trained_std)
    ])
    return train_transforms, val_transforms


class MaskDataset(Dataset):
    def __init__(self, filenames, transform):
        self.filenames = filenames
        self.transform = transform
    
    def __len__(self):
        return len(self.filenames)
    
    def __getitem__(self, idx: int):
        filename = self.filenames[idx]
        filename = str(filename)

        #set labes for images mask vs. no-mask based upon directory affiliation
        #this stupid thing was writen with the wrong slash / not \ for windows? ABSOLOUTELY FRUSTRATING
        label = 1 if 'up_mask' in filename.split('\\') else 0
        
#         if label == 1:
#             print(label)
            
#         print(filename)

        image = cv2.imread(filename)
        image = Image.fromarray(image)
        image = self.transform(image)
        label = torch.tensor(label)
        
#         return image, label
        return {'image': image, 'label': label, 'filename': filename}
    

def build_dataloaders(dataset_path, batch_size):

    #get the composed transforms for training and validation(just normalization)
    t_transforms, v_transforms = compose_transforms()

    #collect the files from the training set and send to dataloader/MaskDataset class
    train_filenames = get_files(f"{dataset_path}train/")
    trainset_class = MaskDataset(train_filenames, transform=t_transforms)
    train_dl = DataLoader(trainset_class, batch_size=batch_size, sampler=RandomSampler(trainset_class), collate_fn=collate_fn)
    
    print("train data: ", len(trainset_class))
    
    #collect the files from the validation set and send to dataloader/MaskDataset class
    val_filenames = get_files(f"{dataset_path}val/")
    valset_class = MaskDataset(val_filenames, transform=v_transforms)
    val_dl = DataLoader(valset_class, batch_size=batch_size, sampler=RandomSampler(valset_class), collate_fn=collate_fn)
    
    print("val data: ", len(valset_class))
    
    return train_dl, val_dl


def get_files(dataset_path):
    files = [] #empty list to accumulate all the image_paths
 
    data_path = Path(dataset_path) #pathify it

    mask_images =  collect_files(data_path / 'up_mask/', '*.png') #use helper fn
    print(mask_images)
    no_mask_images = collect_files(data_path / 'no_mask/', '*.png') #use helper fn
    
    files += mask_images
    files += no_mask_images
        
    assert len(files) != 0, f'No images were collected! Check this path: {dataset_path}'
    
    np.random.shuffle(files)

    return files

def collect_files(file_dir_path, file_pattern): 
    return list(file_dir_path.glob(file_pattern))

In [242]:
# sample = next(iter(MaskDataset(train_filenames, transform=t_transforms)))
# print("length of sample: ", len(sample))


In [243]:
# image, label = sample
# print(image.shape)
# print(label.shape)

In [244]:
dataset_path = "E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/"
batch_size=32
train_dl, val_dl = build_dataloaders(dataset_path, batch_size)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2aflinlpgmn.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2bgndykcvoy.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2cfyyczqoii.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2cjudlxepek.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2cxkglksohx.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2dfimrmhxuc.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2ducegkiath.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/val/up_mask/maksssksksss103_2dxijexshlv.png'), WindowsPath('E:/One Drive/OneDrive/Mainproject/MaskLockData/dataset2/va

val data:  20434


In [245]:
batch = next(iter(train_dl))

print("length of batch: ", len(batch))

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
length of batch:  3


In [246]:
# images, labels = batch

# print('types:', type(images), type(labels))
# print('shapes:', images.shape, labels.shape)

In [247]:
# images, labels = batch
# print(images.shape)
# print(labels.shape)

In [248]:

# step, data = enumerate(train_dl)

# inputs = data[0]
# labels = data[1]

In [249]:
progress_bar = tqdm(train_dl, total=int(len(train_dl)), desc='Train Epoch')

In [250]:
def test(progress_bar):
    for step, data in enumerate(progress_bar):
            #colledt data
            inputs = data['image']
            labels = data['label'].view(-1)

#             print(inputs)
#             print(labels.numpy())
            arr = labels.numpy()
            if 1 in arr:
                print(arr)
                return 0
            elif step == 3000:
                print("-")
                return 0
            

In [251]:
test(progress_bar)

1
1
1
1
1
1
1
1
1
1
1
1
[1 0 0 0 1 0 1 0 1 0 0 1 1 0 1 1 0 0 0 1 1 0 0 0 0 0 1 0 0 0 1 0]



0